# In this file we test all NFT functions from nft_analyse.py

## Import

In [1]:
import sys
# adding signal_handling to the system path
sys.path.insert(0, '../signal_handling/')
sys.path.insert(0, '../nft_handling/')
sys.path.insert(0, '../PJTpy/')

from FNFTpy_extended import nsev_poly
from FNFTpy import nsev, nsev_inverse, nsev_inverse_xi_wrapper
import numpy as np
import pandas as pd
import random
import timeit
from tqdm import tqdm
from scipy.fft import fft, ifft, fftfreq, fftshift, ifftshift

import matplotlib.pyplot as plt
import matplotlib
import plotly.express as px
import plotly.graph_objects as go

from importlib import reload

import ssfm
reload(ssfm)

import ssfm_gpu
reload(ssfm_gpu)

import signal_generation as sg
reload(sg)

import nft_analyse as nft
reload(nft)

import test_signals
reload(test_signals)
from PJTpy import pjt

## Create signal

In [13]:
reload(ssfm_gpu)

ampl = 5.45
chirp = 0.0

t_span = 64.0
n_t = 2 ** 10

dt = t_span / n_t
t = np.array([(i + 0) * dt - t_span / 2 for i in range(n_t)])
print("t =", t[0], t[-1], len(t))

xi_span = np.pi / dt
n_xi = n_t # 2 ** 8
d_xi = xi_span / n_xi
xi = np.array([(i + 1) * d_xi - xi_span / 2. for i in range(n_xi)])
print("xi_old  =", xi[0], xi[-1])
# For FNFT (the same + d_xi to all values)
rv, xi_val = nsev_inverse_xi_wrapper(n_t, t[0], t[-1], n_xi)
xi = xi_val[0] + np.arange(n_xi) * (xi_val[1] - xi_val[0]) / (n_xi - 1)
d_xi = xi[1] - xi[0]

print("xi_fnft =", xi[0], xi[-1])

angle = 0 # np.pi / 3

q1, a_xi, b_xi, xi_discr, b_discr, r_discr, ad_discr = test_signals.get_sech(t, xi, a=ampl, c=chirp)
q1 *= np.exp(1j*np.pi/3 + 2j*t)
q1 = np.roll(q1, -int(n_t/30))

q2 = q1 * np.sin(angle)
q1 *= np.cos(angle)


print(len(xi_discr), xi_discr)
z_prop = 1
q1_prop, q2_prop = ssfm_gpu.ssfm_gpu.tf_manakov_fiber_propogate(q1, q2, t_span, z_prop, n_steps=2 ** 11, gamma=9/8, beta2=-1)
# q1_prop = ssfm.fiber_propagate(q1, t_span, z_prop, n_span=2 ** 9, gamma=1, beta2=-1)

fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.real(q1), name="q1_re"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q1), name="q1_im"))
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.real(q2), name="q2_re"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q2), name="q2_im"))
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.real(q1_prop), name="q1_prop_re"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q1_prop), name="q1_prop_im"))
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.real(q2_prop), name="q2_prop_re"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q2_prop), name="q2_prop_im"))
fig.show()

t = -32.0 31.9375 1024
xi_old  = -25.083653843506003 25.132741228718345
xi_fnft = -25.083653843506006 25.132741228718345
5 [0.+4.95j 0.+3.95j 0.+2.95j 0.+1.95j 0.+0.95j]


## WITHOUT PROPAGATION

In [24]:
import nft_analyse as nft
# reload(nft)

xi_upsampling = 1
forward_continuous_type= 'fnft' #'fnft' 'slow'
forward_discrete_type='pjt' # 'fnft' 'pjt'
forward_discrete_coef_type='bi-direct'
inverse_type='both'
fnft_type=27 # 0 = MOD_AL, 5 = 2SPLIT2B, 21 = 4SPLIT4B, 27 = TES4
nft_type='tes4'
use_contour = False
n_discrete_skip = 2

res_dbp = nft.make_dbp_nft(t, -z_prop, q1, q2, xi_upsampling=xi_upsampling,
                           forward_continuous_type=forward_continuous_type,
                           forward_discrete_type=forward_discrete_type,
                           forward_discrete_coef_type=forward_discrete_coef_type,
                           inverse_type=inverse_type,
                           fnft_type=fnft_type, nft_type=nft_type,
                           use_contour=use_contour, n_discrete_skip=n_discrete_skip,
                           print_sys_message=True)

q1_tib_total = res_dbp['q_total'][0]
q1_tib_left = res_dbp['q_tib_left'][0]
q1_tib_right = res_dbp['q_tib_right'][0]

q2_tib_total = res_dbp['q_total'][1]
q2_tib_left = res_dbp['q_tib_left'][1]
q2_tib_right = res_dbp['q_tib_right'][1]

b1 = res_dbp['b_prop'][0]
b2 = res_dbp['b_prop'][1]
a = res_dbp['a']

xi_d_calculated = res_dbp['xi_d']
print("eig_num:", xi_d_calculated)
print("eig_exact:", xi_discr)
print("bd_num:", res_dbp['bd_prop'])
print("rd_num:", res_dbp['bd_prop'] / res_dbp['ad'])
print("bd_right_num:", res_dbp['bd_right_prop'])
print("b_prop =", res_dbp['b_prop'][0][int(n_t/2)])
print("q_tib_total=", q1_tib_total[int(n_t/2)])

#######################

res_dbp = nft.make_dbp_nft(t, -z_prop, q1, xi_upsampling=xi_upsampling,
                           forward_continuous_type=forward_continuous_type,
                           forward_discrete_type=forward_discrete_type,
                           forward_discrete_coef_type=forward_discrete_coef_type,
                           inverse_type=inverse_type,
                           fnft_type=fnft_type, nft_type=nft_type,
                           use_contour=use_contour, n_discrete_skip=n_discrete_skip,
                           print_sys_message=True)

q1_fnft = res_dbp['q_fnft']
q1_tib_total_NLSE = res_dbp['q_total']

print(np.shape(b_xi), np.shape(xi))

Time to calculate discrete spectrum 829.808 ms
Time to calculate continuous spectrum 2412.5209999999997 ms
Number of discrete eigenvalues: 5
Time to calculate continuous part of Omega 1.032 ms
Time to calculate discrete part of Omega 0.0 ms
Time to calculate TIB 1.9919999999999998 ms
Time to calculate continuous part of Omega 0.9970000000000001 ms
Time to calculate discrete part of Omega 0.967 ms
Time to calculate TIB 1.9940000000000002 ms
Time to calculate all TIBs 6.982 ms
eig_num: [-0.99999738+4.94997172j -0.99999957+3.94997466j -1.00000064+2.94997567j
 -1.00000088+1.9499757j  -1.00000056+0.94997545j]
eig_exact: [0.+4.95j 0.+3.95j 0.+2.95j 0.+1.95j 0.+0.95j]
bd_num: [[ 0.13017835+0.25924707j -0.37192844-0.0207461j   0.13290115+0.45948042j
  -0.05738147+0.61148138j -0.29961029-0.72947174j]
 [ 0.        -0.j         -0.        +0.j          0.        -0.j
   0.        +0.j          0.        +0.j        ]]
rd_num: [[-318.85887746+160.10840794j  -51.04605684+914.99599363j
  -755.852781

In [23]:
q1_tib_total

array([-0.00322146-0.01318431j, -0.00154221-0.01339313j,
        0.00013869-0.01339096j, ..., -0.00254452+0.01342425j,
       -0.00422654+0.0130896j , -0.00586464+0.01254421j])

In [21]:
color = ['red', 'blue', 'green', 'xkcd:light purple', 'xkcd:cyan', 'xkcd:lime green']
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.real(q1_tib_total), name="q1_tib_total"))
#fig.add_trace(go.Scatter(x=t, y=np.real(q1_tib_left), name="q1_tib_left"))
#fig.add_trace(go.Scatter(x=t, y=np.real(q1_tib_right), name="q1_tib_right"))
fig.add_trace(go.Scatter(x=t, y=np.real(q1_tib_total_NLSE), name="q1_tib_total_NLSE"))
fig.add_trace(go.Scatter(x=t, y=np.real(q1_fnft), name="q1_fnft"))
fig.add_trace(go.Scatter(x=t, y=np.real(q1_prop), name="q1_prop"))
fig.show()

color = ['red', 'blue', 'green', 'xkcd:light purple', 'xkcd:cyan', 'xkcd:lime green']
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.imag(q1_tib_total), name="q1_tib_total"))
#fig.add_trace(go.Scatter(x=t, y=np.imag(q1_tib_left), name="q1_tib_left"))
#fig.add_trace(go.Scatter(x=t, y=np.imag(q1_tib_right), name="q1_tib_right"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q1_tib_total_NLSE), name="q1_tib_total_NLSE"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q1_fnft), name="q1_fnft"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q1_prop), name="q1_prop"))
fig.show()

color = ['red', 'blue', 'green', 'xkcd:light purple', 'xkcd:cyan', 'xkcd:lime green']
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.absolute(q1_prop - q1_tib_total), name="q1_tib_total"))
fig.add_trace(go.Scatter(x=t, y=np.absolute(q1_prop - q1_tib_total_NLSE), name="q1_tib_total_NLSE"))
fig.add_trace(go.Scatter(x=t, y=np.absolute(q1_prop - q1_fnft), name="q1_fnft"))
fig.show()

In [136]:
color = ['red', 'blue', 'green', 'xkcd:light purple', 'xkcd:cyan', 'xkcd:lime green']
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.real(q2_tib_total), name="q2_tib_total"))
fig.add_trace(go.Scatter(x=t, y=np.real(q2_tib_left), name="q2_tib_left"))
fig.add_trace(go.Scatter(x=t, y=np.real(q2_tib_right), name="q2_tib_right"))
#fig.add_trace(go.Scatter(x=t, y=np.real(q_fnft_still), name="q_fnft_still"))
fig.add_trace(go.Scatter(x=t, y=np.real(q2_prop), name="q2_prop"))
fig.show()

color = ['red', 'blue', 'green', 'xkcd:light purple', 'xkcd:cyan', 'xkcd:lime green']
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.imag(q2_tib_total), name="q2_tib_total"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q2_tib_left), name="q2_tib_left"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q2_tib_right), name="q2_tib_right"))
#fig.add_trace(go.Scatter(x=t, y=np.imag(q_fnft_still), name="q_fnft_still"))
fig.add_trace(go.Scatter(x=t, y=np.imag(q2_prop), name="q2_prop"))
fig.show()

color = ['red', 'blue', 'green', 'xkcd:light purple', 'xkcd:cyan', 'xkcd:lime green']
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.absolute(q2_prop - q2_tib_total), name="q2_tib_total"))
#fig.add_trace(go.Scatter(x=t, y=np.absolute(q - q_fnft_still), name="q_fnft_still"))
fig.show()

In [33]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.real(b1), name="b1_re"))
fig.add_trace(go.Scatter(x=t, y=np.imag(b1), name="b1_im"))
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.real(b2), name="b2_re"))
fig.add_trace(go.Scatter(x=t, y=np.imag(b2), name="b2_im"))
fig.show()

fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.real(a), name="a_re"))
fig.add_trace(go.Scatter(x=t, y=np.imag(a), name="a_im"))
fig.show()